# Gaps in plot
> Why do the mixture embeddings look like that?

This notebook is mostly to explore the white space in the plot. I am looking for
alternatives to grabbing the points with the lasso tool, but it is what it is.

In parallel, I am running a double-precision version of the code to see if that
will remove the plots instead. Floating point weirdness is my top guess right
now.

In [1]:
!pip install ipympl

In [2]:
%load_ext autoreload
%autoreload 2
%matplotlib widget

In [3]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import anndata
import plotly


In [4]:
adata = anndata.read_h5ad("data/big_table_with_embeddings.h5ad")


In [5]:
embed = adata.obsm["geomstats_hyperboloid_mix_CONVERTED_2_100iter"]

# fig = plt.figure(figsize=(10, 10))
# plt.scatter(embed[:, 0], embed[:, 1], s=1, alpha=0.1)

# Plot with plotly and grab regions with lasso
import plotly.express as px

px.scatter(
    x=embed[:, 0],
    y=embed[:, 1],
    opacity=0.1,
    width=800,
    height=800,
    render_mode="webgl",
)


In [6]:
# # Grabber code

# import pandas as pd
# import plotly.graph_objects as go
# from dash import Dash, html, dcc, callback, Output, Input, jupyter_dash

# # jupyter_dash.default_mode="external"

# # Init app
# app = Dash(__name__)

# # Create a dash application
# app.layout = html.Div([
#     dcc.Graph(
#         id='scatter-plot',
#         figure={
#             'data': [
#                 go.Scattergl(
#                     x = embed[:,0],
#                     y = embed[:,1],
#                     mode = 'markers',
#                     marker = dict(size = 2),
#                     text = adata.obs.index,
#                     customdata = adata.obs.index
#                 )
#             ],
#             'layout': go.Layout(
#                 dragmode = 'lasso'  # Enable lasso selection by default
#             )
#         }
#     ),
#     html.Pre(id='selection', style={'overflowY': 'scroll', 'height': '300px'})
# ])

# @app.callback(
#     Output('selection', 'children'),
#     [Input('scatter-plot', 'selectedData')]
# )
# def display_selected_data(selectedData):
#     if selectedData:
#         points = selectedData['points']
#         ids = [point['customdata'] for point in points]
#         return '\n'.join(ids)

# # Run the app inline in Jupyter notebook
# app.run_server(mode='inline')


I used the above code to lasso the points of interest, then saved the IDs in `data/clusternames`. I found 7 clusters in total

In [8]:
# # Check that the clusters check out
# from geomstats.geometry.hyperbolic import Hyperbolic

# adata.obs["cluster"] = None
# for i in range(1,8):
#     ids = pd.read_csv(f"data/clusternames/c{i}.txt", header=None)[0].values
#     adata.obs.loc[ids, "cluster"] = i

# # Fill in blank clusters
# none_ids = adata.obs[adata.obs["cluster"].isnull()].index
# notnone_ids = adata.obs[adata.obs["cluster"].notnull()].index
# notnone_embeds = adata[notnone_ids].obsm["geomstats_hyperboloid_mix_CONVERTED_2_100iter"]
# manifold = Hyperbolic(dim=2, default_coords_type="ball")
# for obs_id in none_ids:
#     # Find distances to all other points
#     dists = manifold._metric.dist(
#         notnone_embeds,
#         adata[obs_id].obsm["geomstats_hyperboloid_mix_CONVERTED_2_100iter"]
#     )
#     # Find min
#     min_id = notnone_ids[np.argmin(dists)]
#     adata.obs.loc[obs_id, "cluster"] = adata.obs.loc[min_id, "cluster"]
#     print(f"Assigned {obs_id} to {adata.obs.loc[min_id, 'cluster']}")

# Convert to categorical
adata.obs["cluster"] = adata.obs["cluster"].astype("category")


# Statistical testing of clusters

In [12]:
# Are the clusters correlated with anything? - handle categorical data

dtypes = adata.obs.dtypes
numeric_cols = adata.obs.select_dtypes(include=np.number)
categorical_cols = adata.obs.select_dtypes(include=["object", "category"])

print(len(numeric_cols.columns), len(categorical_cols.columns), len(dtypes))
# 58 + 697 = 755 - checks out


58 697 755


In [35]:
# Numeric versions

from scipy.stats import chi2_contingency, f_oneway, kruskal

# Numeric case
numeric_stats = pd.DataFrame(
    index=numeric_cols.columns, columns=["coefficient", "p_value", "n"]
)
for column in numeric_cols:
    # Remove nans and aggregate into lists
    small_df = adata.obs[["cluster", column]].dropna()
    values = small_df.groupby("cluster")[column].apply(list).tolist()
    # Perform Kruskal-Wallis test
    try:
        coefficient, p_value = kruskal(*values)
    except ValueError:
        coefficient = p_value = None
    numeric_stats.loc[column] = {
        "coefficient": coefficient, "p_value": p_value, "n": len(small_df)
    }

# Categorical case
categorical_stats = pd.DataFrame()
print("Done")
numeric_stats

Done


coefficient   p_value        n
age_years                                  NaN       NaN     12.0
animal_free_text                           NaN       NaN      0.0
animal_type_free_text                      NaN       NaN      0.0
bmi                                        NaN       NaN      0.0
body_product                               NaN       NaN      0.0
body_site                                  NaN       NaN      0.0
covid_occupation                           NaN       NaN      0.0
covid_suspected_positive_date              NaN       NaN      0.0
covid_symptoms_other                       NaN       NaN      0.0
elevation                            19.430724  0.003495   3160.0
fermented_consumed                         NaN       NaN      0.0
fermented_consumed_other                   NaN       NaN      0.0
fermented_other                            NaN       NaN      0.0
fermented_produce_commercial               NaN       NaN      0.0
fermented_produce_commercial_other         NaN       NaN      0.0
fermented_produce_personal                 NaN       NaN      0.0
fermented_produce_personal_other           NaN       NaN      0.0
food_source                                NaN       NaN      0.0
food_special                               NaN       NaN      0.0
height_cm                                  NaN       NaN      0.0
height_units                               NaN       NaN      0.0
host_taxid                                 NaN       NaN  29394.0
humans_free_text                           NaN       NaN      0.0
name                                       NaN       NaN      0.0
other_animals_free_text                    NaN       NaN      0.0
pm_gastro_problems                         NaN       NaN      0.0
pm_lifestyle_change_how                    NaN       NaN      0.0
pm_participation_reason                    NaN       NaN      0.0
pm_shared_pcp                              NaN       NaN      0.0
pm_shared_pcp_changes                      NaN       NaN      0.0
pm_shared_pcp_changes_what                 NaN       NaN      0.0
pm_shared_who                              NaN       NaN      0.0
qiita_study_id                             NaN       NaN  32608.0
vioscreen_activity_level                   NaN       NaN      0.0
vioscreen_age                              NaN       NaN      0.0
vioscreen_bcodeid                          NaN       NaN      0.0
vioscreen_bmi                              NaN       NaN      0.0
vioscreen_dob                              NaN       NaN      0.0
vioscreen_eer                              NaN       NaN      0.0
vioscreen_email                            NaN       NaN      0.0
vioscreen_finished                         NaN       NaN      0.0
vioscreen_gender                           NaN       NaN      0.0
vioscreen_height                           NaN       NaN      0.0
vioscreen_nutrient_recommendation          NaN       NaN      0.0
vioscreen_procdate                         NaN       NaN      0.0
vioscreen_protocol                         NaN       NaN      0.0
vioscreen_recno                            NaN       NaN      0.0
vioscreen_scf                              NaN       NaN      0.0
vioscreen_scfv                             NaN       NaN      0.0
vioscreen_srvid                            NaN       NaN      0.0
vioscreen_started                          NaN       NaN      0.0
vioscreen_subject_id                       NaN       NaN      0.0
vioscreen_time                             NaN       NaN      0.0
vioscreen_user_id                          NaN       NaN      0.0
vioscreen_visit                            NaN       NaN      0.0
vioscreen_weight                           NaN       NaN      0.0
weight_kg                                  NaN       NaN      0.0
weight_units                               NaN       NaN      0.0